In [2]:
import os
import time
import csv
import concurrent.futures
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains

# Function to scrape data for a single account
def scrape_account(account_num):
    # Initialize Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--disable-notifications")

    # Initialize the WebDriver
    driver = webdriver.Chrome(options=chrome_options)

    try:
        website = f'https://www.thebluebook.com/iProView/{account_num}/crawford-tracey-corp/subcontractors/locations-contacts/'

        # Open the website for the current account
        driver.get(website)

        # Wait for the contact page to load completely
        try:
            WebDriverWait(driver, 5).until(EC.presence_of_element_located((By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3')))
        except TimeoutException:
            return None

        # Scrape specific text using the provided XPaths
        account_name = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3').text
        address = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[1]').text

        try:
            acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[2]/div[1]/a/span')
            if acc_number_element.text == 'View Phone':
                # Scroll to the element
                action = ActionChains(driver)
                action.move_to_element(acc_number_element).perform()

                # Click the element to reveal the phone number
                driver.execute_script("arguments[0].click();", acc_number_element)
                time.sleep(2)  # Wait for the number to load

                # Check if FaceTime modal appears
                is_facetime_modal = False
                try:
                    facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                    if facetime_modal.is_displayed():
                        is_facetime_modal = True
                except NoSuchElementException:
                    pass

                # If it's FaceTime modal, go back and try a different approach
                if is_facetime_modal:
                    # Go back to the previous page
                    driver.back()
                    return None
                else:
                    # Find the element containing the phone number
                    acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[2]/div[1]/a/span[2]')
            acc_number = acc_number_element.text
        except NoSuchElementException:
            acc_number = None
        company_info = driver.find_element(By.XPATH, '//*[@id="companyInfoSection"]/div/ul').text

        # Initialize website variable
        website = None

        # Scrape website if available
        try:
            website_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[3]/a')
            website = website_element.get_attribute('href')
        except NoSuchElementException:
            pass

        # Scrape industry if available
        try:
            industry_element = driver.find_element(By.XPATH, '//*[@id="proViewBreadCrumbs"]/a[3]')
            industry = industry_element.text
        except NoSuchElementException:
            industry = ''

        # Scrape contacts
        contacts = []
        for i in range(1, 8):  # There are 7 contacts based on provided XPaths
            name_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/button'
            title_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[1]'
            number_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[2]/a/span'

            try:
                name = driver.find_element(By.XPATH, name_xpath).text
                title = driver.find_element(By.XPATH, title_xpath).text

                # Check if the text is "View Phone"
                number_element = driver.find_element(By.XPATH, number_xpath)
                if number_element.text == 'View Phone':
                    # Scroll to the element
                    action = ActionChains(driver)
                    action.move_to_element(number_element).perform()

                    # Click the element to reveal the phone number
                    driver.execute_script("arguments[0].click();", number_element)
                    time.sleep(2)  # Wait for the number to load

                    # Check if FaceTime modal appears
                    is_facetime_modal = False
                    try:
                        facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                        if facetime_modal.is_displayed():
                            is_facetime_modal = True
                    except NoSuchElementException:
                        pass

                    # If it's FaceTime modal, skip this contact
                    if is_facetime_modal:
                        continue
                    else:
                        # Find the element containing the phone number
                        number_element = driver.find_element(By.XPATH, f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div[1]/div/div/div/div[2]/a[1]/span[2]')
                number = number_element.text

                contacts.append({'Name': name, 'Title': title, 'Number': number})
            except NoSuchElementException:
                continue

        # Return the scraped data
        return {'account_num': account_num, 'account_name': account_name, 'address': address, 'acc_number': acc_number, 'company_info': company_info, 'website': website, 'industry': industry, 'contacts': contacts}

    finally:
        driver.quit()

# Set the directory to save the CSV file
save_dir = '/Users/safi.uddin/Desktop/bb_scrape'
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

# Open the CSV file in write mode
with open(os.path.join(save_dir, 'contacts.csv'), 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['ID', 'Name', 'Title', 'Number', 'Account Name', 'Address', 'Account number', 'Company Info', 'Website', 'Industry']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

    # Define the range of accounts
    account_range = range(227000,230000)

    # Initialize ThreadPoolExecutor
    with concurrent.futures.ThreadPoolExecutor() as executor:
        # Submit scraping tasks
        futures = {executor.submit(scrape_account, account_num): account_num for account_num in account_range}

        # Iterate over completed tasks
        for future in concurrent.futures.as_completed(futures):
            account_num = futures[future]
            try:
                result = future.result()
                if result:  # Check if scraping was successful
                    if not result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': '', 'Title': '', 'Number': '', 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
                    for contact in result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': contact['Name'], 'Title': contact['Title'], 'Number': contact['Number'], 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
            except Exception as e:
                print(f"Failed to scrape account {account_num}: {e}")

# Delay to ensure all threads finish before quitting
time.sleep(5)


Failed to scrape account 35025: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x000000010452e940 chromedriver + 4368704
1   chromedriver                        0x0000000104526dd4 chromedriver + 4337108
2   chromedriver                        0x000000010414ac04 chromedriver + 289796
3   chromedriver                        0x0000000104125918 chromedriver + 137496
4   chromedriver                        0x00000001041b1ab8 chromedriver + 711352
5   chromedriver                        0x00000001041c4d08 chromedriver + 789768
6   chromedriver                        0x0000000104181ab4 chromedriver + 514740
7   chromedriver                        0x000000010418250c chromedriver + 517388
8   chromedriver                        0x00000001044f2e5c chromedriver + 4124252
9   chromedriver                        0x00000001044f7c4c chromedriver + 4144204
10  chrom

Failed to scrape account 35052: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000102e82940 chromedriver + 4368704
1   chromedriver                        0x0000000102e7add4 chromedriver + 4337108
2   chromedriver                        0x0000000102a9ec04 chromedriver + 289796
3   chromedriver                        0x0000000102a79918 chromedriver + 137496
4   chromedriver                        0x0000000102b05ab8 chromedriver + 711352
5   chromedriver                        0x0000000102b18d08 chromedriver + 789768
6   chromedriver                        0x0000000102ad5ab4 chromedriver + 514740
7   chromedriver                        0x0000000102ad650c chromedriver + 517388
8   chromedriver                        0x0000000102e46e5c chromedriver + 4124252
9   chromedriver                        0x0000000102e4bc4c chromedriver + 4144204
10  chrom

Failed to scrape account 35049: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x00000001047a2940 chromedriver + 4368704
1   chromedriver                        0x000000010479add4 chromedriver + 4337108
2   chromedriver                        0x00000001043bec04 chromedriver + 289796
3   chromedriver                        0x0000000104399918 chromedriver + 137496
4   chromedriver                        0x0000000104425ab8 chromedriver + 711352
5   chromedriver                        0x0000000104438d08 chromedriver + 789768
6   chromedriver                        0x00000001043f5ab4 chromedriver + 514740
7   chromedriver                        0x00000001043f650c chromedriver + 517388
8   chromedriver                        0x0000000104766e5c chromedriver + 4124252
9   chromedriver                        0x000000010476bc4c chromedriver + 4144204
10  chrom

Failed to scrape account 35075: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000104a42940 chromedriver + 4368704
1   chromedriver                        0x0000000104a3add4 chromedriver + 4337108
2   chromedriver                        0x000000010465ec04 chromedriver + 289796
3   chromedriver                        0x0000000104639918 chromedriver + 137496
4   chromedriver                        0x00000001046c5ab8 chromedriver + 711352
5   chromedriver                        0x00000001046d8d08 chromedriver + 789768
6   chromedriver                        0x0000000104695ab4 chromedriver + 514740
7   chromedriver                        0x000000010469650c chromedriver + 517388
8   chromedriver                        0x0000000104a06e5c chromedriver + 4124252
9   chromedriver                        0x0000000104a0bc4c chromedriver + 4144204
10  chrom

Failed to scrape account 35121: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000100e6e940 chromedriver + 4368704
1   chromedriver                        0x0000000100e66dd4 chromedriver + 4337108
2   chromedriver                        0x0000000100a8ac04 chromedriver + 289796
3   chromedriver                        0x0000000100a65918 chromedriver + 137496
4   chromedriver                        0x0000000100af1ab8 chromedriver + 711352
5   chromedriver                        0x0000000100b04d08 chromedriver + 789768
6   chromedriver                        0x0000000100ac1ab4 chromedriver + 514740
7   chromedriver                        0x0000000100ac250c chromedriver + 517388
8   chromedriver                        0x0000000100e32e5c chromedriver + 4124252
9   chromedriver                        0x0000000100e37c4c chromedriver + 4144204
10  chrom

...

Failed to scrape account 35181: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000102986940 chromedriver + 4368704
1   chromedriver                        0x000000010297edd4 chromedriver + 4337108
2   chromedriver                        0x00000001025a2c04 chromedriver + 289796
3   chromedriver                        0x000000010257d918 chromedriver + 137496
4   chromedriver                        0x0000000102609ab8 chromedriver + 711352
5   chromedriver                        0x000000010261cd08 chromedriver + 789768
6   chromedriver                        0x00000001025d9ab4 chromedriver + 514740
7   chromedriver                        0x00000001025da50c chromedriver + 517388
8   chromedriver                        0x000000010294ae5c chromedriver + 4124252
9   chromedriver                        0x000000010294fc4c chromedriver + 4144204
10  chrom

Failed to scrape account 35188: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000100c1e940 chromedriver + 4368704
1   chromedriver                        0x0000000100c16dd4 chromedriver + 4337108
2   chromedriver                        0x000000010083ac04 chromedriver + 289796
3   chromedriver                        0x0000000100815918 chromedriver + 137496
4   chromedriver                        0x00000001008a1ab8 chromedriver + 711352
5   chromedriver                        0x00000001008b4d08 chromedriver + 789768
6   chromedriver                        0x0000000100871ab4 chromedriver + 514740
7   chromedriver                        0x000000010087250c chromedriver + 517388
8   chromedriver                        0x0000000100be2e5c chromedriver + 4124252
9   chromedriver                        0x0000000100be7c4c chromedriver + 4144204
10  chrom

Failed to scrape account 35509: Message: timeout: Timed out receiving message from renderer: 283.697
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000100fc2940 chromedriver + 4368704
1   chromedriver                        0x0000000100fbadd4 chromedriver + 4337108
2   chromedriver                        0x0000000100bdec04 chromedriver + 289796
3   chromedriver                        0x0000000100bc809c chromedriver + 196764
4   chromedriver                        0x0000000100be8bd0 chromedriver + 330704
5   chromedriver                        0x0000000100c597b8 chromedriver + 792504
6   chromedriver                        0x0000000100c15ab4 chromedriver + 514740
7   chromedriver                        0x0000000100c1650c chromedriver + 517388
8   chromedriver                        0x0000000100f86e5c chromedriver + 4124252
9   chromedriver                        0x0000000100f8bc4c chromedriver + 4144204
10  chromedriver                 

Failed to scrape account 35703: Message: timeout: Timed out receiving message from renderer: 298.270
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x0000000104b76940 chromedriver + 4368704
1   chromedriver                        0x0000000104b6edd4 chromedriver + 4337108
2   chromedriver                        0x0000000104792c04 chromedriver + 289796
3   chromedriver                        0x000000010477d230 chromedriver + 201264
4   chromedriver                        0x000000010477cf5c chromedriver + 200540
5   chromedriver                        0x000000010477ad20 chromedriver + 191776
6   chromedriver                        0x000000010477b7f0 chromedriver + 194544
7   chromedriver                        0x000000010478a174 chromedriver + 254324
8   chromedriver                        0x000000010479cf4c chromedriver + 331596
9   chromedriver                        0x000000010477be38 chromedriver + 196152
10  chromedriver                   

Failed to scrape account 35747: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=124.0.6367.208)
Stacktrace:
0   chromedriver                        0x00000001027a2940 chromedriver + 4368704
1   chromedriver                        0x000000010279add4 chromedriver + 4337108
2   chromedriver                        0x00000001023bec04 chromedriver + 289796
3   chromedriver                        0x0000000102399918 chromedriver + 137496
4   chromedriver                        0x0000000102425ab8 chromedriver + 711352
5   chromedriver                        0x0000000102438d08 chromedriver + 789768
6   chromedriver                        0x00000001023f5ab4 chromedriver + 514740
7   chromedriver                        0x00000001023f650c chromedriver + 517388
8   chromedriver                        0x0000000102766e5c chromedriver + 4124252
9   chromedriver                        0x000000010276bc4c chromedriver + 4144204
10  chrom

In [ ]:
import os
import time
import csv
import concurrent.futures
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains

# Function to scrape data for a single account
def scrape_account(account_num):
    # Initialize Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--disable-notifications")

    # Initialize the WebDriver
    driver = webdriver.Chrome(options=chrome_options)
    time.sleep(5)

    try:
        website = f'https://www.thebluebook.com/iProView/{account_num}/crawford-tracey-corp/subcontractors/locations-contacts/'

        # Open the website for the current account
        driver.get(website)

        # Wait for the contact page to load completely
        try:
            WebDriverWait(driver, 2).until(EC.presence_of_element_located((By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3')))
        except TimeoutException:
            return None

        # Scrape specific text using the provided XPaths
        account_name = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3').text
        address = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[1]').text

        try:
            acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[2]/div[1]/a/span')
            if acc_number_element.text == 'View Phone':
                # Scroll to the element
                action = ActionChains(driver)
                action.move_to_element(acc_number_element).perform()

                # Click the element to reveal the phone number
                driver.execute_script("arguments[0].click();", acc_number_element)
                time.sleep(2)  # Wait for the number to load

                # Check if FaceTime modal appears
                is_facetime_modal = False
                try:
                    facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                    if facetime_modal.is_displayed():
                        is_facetime_modal = True
                except NoSuchElementException:
                    pass

                # If it's FaceTime modal, go back and try a different approach
                if is_facetime_modal:
                    # Go back to the previous page
                    driver.back()
                    return None
                else:
                    # Find the element containing the phone number
                    acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[2]/div[1]/a/span[2]')
            acc_number = acc_number_element.text
        except NoSuchElementException:
            acc_number = None
        company_info = driver.find_element(By.XPATH, '//*[@id="companyInfoSection"]/div/ul').text

        # Initialize website variable
        website = None

        # Scrape website if available
        try:
            website_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[3]/a')
            website = website_element.get_attribute('href')
        except NoSuchElementException:
            pass

        # Scrape industry if available
        try:
            industry_element = driver.find_element(By.XPATH, '//*[@id="proViewBreadCrumbs"]/a[3]')
            industry = industry_element.text
        except NoSuchElementException:
            industry = ''

        # Scrape contacts
        contacts = []
        for i in range(1, 8):  # There are 7 contacts based on provided XPaths
            name_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/button'
            title_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[1]'
            number_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[2]/a/span'

            try:
                name = driver.find_element(By.XPATH, name_xpath).text
                title = driver.find_element(By.XPATH, title_xpath).text

                # Check if the text is "View Phone"
                number_element = driver.find_element(By.XPATH, number_xpath)
                if number_element.text == 'View Phone':
                    # Scroll to the element
                    action = ActionChains(driver)
                    action.move_to_element(number_element).perform()

                    # Click the element to reveal the phone number
                    driver.execute_script("arguments[0].click();", number_element)
                    time.sleep(2)  # Wait for the number to load

                    # Check if FaceTime modal appears
                    is_facetime_modal = False
                    try:
                        facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                        if facetime_modal.is_displayed():
                            is_facetime_modal = True
                    except NoSuchElementException:
                        pass

                    # If it's FaceTime modal, skip this contact
                    if is_facetime_modal:
                        continue
                    else:
                        # Find the element containing the phone number
                        number_element = driver.find_element(By.XPATH, f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div[1]/div/div/div/div[2]/a[1]/span[2]')
                number = number_element.text

                contacts.append({'Name': name, 'Title': title, 'Number': number})
            except NoSuchElementException:
                continue

        # Return the scraped data
        return {'account_num': account_num, 'account_name': account_name, 'address': address, 'acc_number': acc_number, 'company_info': company_info, 'website': website, 'industry': industry, 'contacts': contacts}

    finally:
        driver.quit()

# Set the directory to save the CSV file
save_dir = '/Users/safi.uddin/Desktop/bb_scrape'
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

# Open the CSV file in write mode
with open(os.path.join(save_dir, 'contacts.csv'), 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['ID', 'Name', 'Title', 'Number', 'Account Name', 'Address', 'Account number', 'Company Info', 'Website', 'Industry']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

    # Define the range of accounts
    account_range = range(422250, 425000)

    # Initialize ThreadPoolExecutor with 50 workers
    with concurrent.futures.ThreadPoolExecutor(max_workers=15) as executor:
        # Submit scraping tasks
        futures = {executor.submit(scrape_account, account_num): account_num for account_num in account_range}

        # Iterate over completed tasks
        for future in concurrent.futures.as_completed(futures):
            account_num = futures[future]
            try:
                result = future.result()
                if result:  # Check if scraping was successful
                    if not result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': '', 'Title': '', 'Number': '', 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
                    for contact in result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': contact['Name'], 'Title': contact['Title'], 'Number': contact['Number'], 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
            except Exception as e:
                print(f"Failed to scrape account {account_num}: {e}")

# Delay to ensure all threads finish before quitting
time.sleep(5)


Failed to scrape account 231158: Message: unknown error: net::ERR_CONNECTION_RESET
  (Session info: chrome=125.0.6422.112)
Stacktrace:
0   chromedriver                        0x000000010256a510 chromedriver + 4302096
1   chromedriver                        0x0000000102562e58 chromedriver + 4271704
2   chromedriver                        0x000000010219419c chromedriver + 278940
3   chromedriver                        0x000000010218d510 chromedriver + 251152
4   chromedriver                        0x000000010217f120 chromedriver + 192800
5   chromedriver                        0x0000000102180480 chromedriver + 197760
6   chromedriver                        0x000000010217f43c chromedriver + 193596
7   chromedriver                        0x000000010217ead0 chromedriver + 191184
8   chromedriver                        0x000000010217ea7c chromedriver + 191100
9   chromedriver                        0x000000010217c85c chromedriver + 182364
10  chromedriver                        0x00000001021

In [ ]:
#use this when you wanna work as well
import os
import time
import csv
import concurrent.futures
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains

# Function to scrape data for a single account
def scrape_account(account_num):
    #Initialize Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--disable-notifications")
    chrome_options.add_argument("--headless")
    chrome_options.add_argument("--disable-gpu")
    chrome_options.add_argument("--window-size=1920x1080")
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")

    # Initialize the WebDriver
    driver = webdriver.Chrome(options=chrome_options)

    try:
        website = f'https://www.thebluebook.com/iProView/{account_num}/crawford-tracey-corp/subcontractors/locations-contacts/'

        # Open the website for the current account
        driver.get(website)

        # Wait for the contact page to load completely
        try:
            WebDriverWait(driver, 5).until(EC.presence_of_element_located((By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3')))
        except TimeoutException:
            return None

        # Scrape specific text using the provided XPaths
        account_name = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3').text
        address = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[1]').text

        try:
            acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[2]/div[1]/a/span')
            if acc_number_element.text == 'View Phone':
                # Scroll to the element
                action = ActionChains(driver)
                action.move_to_element(acc_number_element).perform()

                # Click the element to reveal the phone number
                driver.execute_script("arguments[0].click();", acc_number_element)
                time.sleep(2)  # Wait for the number to load

                # Check if FaceTime modal appears
                is_facetime_modal = False
                try:
                    facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                    if facetime_modal.is_displayed():
                        is_facetime_modal = True
                except NoSuchElementException:
                    pass

                # If it's FaceTime modal, go back and try a different approach
                if is_facetime_modal:
                    # Go back to the previous page
                    driver.back()
                    return None
                else:
                    # Find the element containing the phone number
                    acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[2]/div[1]/a/span[2]')
            acc_number = acc_number_element.text
        except NoSuchElementException:
            acc_number = None
        company_info = driver.find_element(By.XPATH, '//*[@id="companyInfoSection"]/div/ul').text

        # Initialize website variable
        website = None

        # Scrape website if available
        try:
            website_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[3]/a')
            website = website_element.get_attribute('href')
        except NoSuchElementException:
            pass

        # Scrape industry if available
        try:
            industry_element = driver.find_element(By.XPATH, '//*[@id="proViewBreadCrumbs"]/a[3]')
            industry = industry_element.text
        except NoSuchElementException:
            industry = ''

        # Scrape contacts
        contacts = []
        for i in range(1, 8):  # There are 7 contacts based on provided XPaths
            name_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/button'
            title_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[1]'
            number_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[2]/a/span'

            try:
                name = driver.find_element(By.XPATH, name_xpath).text
                title = driver.find_element(By.XPATH, title_xpath).text

                # Check if the text is "View Phone"
                number_element = driver.find_element(By.XPATH, number_xpath)
                if number_element.text == 'View Phone':
                    # Scroll to the element
                    action = ActionChains(driver)
                    action.move_to_element(number_element).perform()

                    # Click the element to reveal the phone number
                    driver.execute_script("arguments[0].click();", number_element)
                    time.sleep(2)  # Wait for the number to load

                    # Check if FaceTime modal appears
                    is_facetime_modal = False
                    try:
                        facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                        if facetime_modal.is_displayed():
                            is_facetime_modal = True
                    except NoSuchElementException:
                        pass

                    # If it's FaceTime modal, skip this contact
                    if is_facetime_modal:
                        continue
                    else:
                        # Find the element containing the phone number
                        number_element = driver.find_element(By.XPATH, f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div[1]/div/div/div/div[2]/a[1]/span[2]')
                number = number_element.text

                contacts.append({'Name': name, 'Title': title, 'Number': number})
            except NoSuchElementException:
                continue

        # Return the scraped data
        return {'account_num': account_num, 'account_name': account_name, 'address': address, 'acc_number': acc_number, 'company_info': company_info, 'website': website, 'industry': industry, 'contacts': contacts}

    finally:
        driver.quit()

# Set the directory to save the CSV file
save_dir = '/Users/safi.uddin/Desktop/bb_scrape'
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

# Open the CSV file in write mode
with open(os.path.join(save_dir, 'contacts.csv'), 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['ID', 'Name', 'Title', 'Number', 'Account Name', 'Address', 'Account number', 'Company Info', 'Website', 'Industry']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

    # Define the range of accounts
    account_range = range(422250, 425000)

    # Initialize ThreadPoolExecutor with as per defined workers
    with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
        # Submit scraping tasks
        futures = {executor.submit(scrape_account, account_num): account_num for account_num in account_range}

        # Iterate over completed tasks
        for future in concurrent.futures.as_completed(futures):
            account_num = futures[future]
            try:
                result = future.result()
                if result:  # Check if scraping was successful
                    if not result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': '', 'Title': '', 'Number': '', 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
                    for contact in result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': contact['Name'], 'Title': contact['Title'], 'Number': contact['Number'], 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
            except Exception as e:
                print(f"Failed to scrape account {account_num}: {e}")

# Delay to ensure all threads finish before quitting
time.sleep(5)


Failed to scrape account 422280: Message: timeout: Timed out receiving message from renderer: 294.541
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x00000001013a6a80 chromedriver + 4385408
1   chromedriver                        0x000000010139f38c chromedriver + 4354956
2   chromedriver                        0x0000000100fbcb0c chromedriver + 281356
3   chromedriver                        0x0000000100fa77c4 chromedriver + 194500
4   chromedriver                        0x0000000100fa73b8 chromedriver + 193464
5   chromedriver                        0x0000000100fa5198 chromedriver + 184728
6   chromedriver                        0x0000000100fa5c4c chromedriver + 187468
7   chromedriver                        0x0000000100fb3fac chromedriver + 245676
8   chromedriver                        0x0000000100fc709c chromedriver + 323740
9   chromedriver                        0x0000000100fa6294 chromedriver + 189076
10  chromedriver   

Failed to scrape account 422313: Message: timeout: Timed out receiving message from renderer: 296.946
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x0000000104b9ea80 chromedriver + 4385408
1   chromedriver                        0x0000000104b9738c chromedriver + 4354956
2   chromedriver                        0x00000001047b4b0c chromedriver + 281356
3   chromedriver                        0x000000010479f7c4 chromedriver + 194500
4   chromedriver                        0x000000010479f3b8 chromedriver + 193464
5   chromedriver                        0x000000010479d198 chromedriver + 184728
6   chromedriver                        0x000000010479dc4c chromedriver + 187468
7   chromedriver                        0x00000001047abfac chromedriver + 245676
8   chromedriver                        0x00000001047bf09c chromedriver + 323740
9   chromedriver                        0x000000010479e294 chromedriver + 189076
10  chromedriver   

Failed to scrape account 422499: Message: timeout: Timed out receiving message from renderer: 294.351
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x0000000100586a80 chromedriver + 4385408
1   chromedriver                        0x000000010057f38c chromedriver + 4354956
2   chromedriver                        0x000000010019cb0c chromedriver + 281356
3   chromedriver                        0x00000001001877c4 chromedriver + 194500
4   chromedriver                        0x00000001001873b8 chromedriver + 193464
5   chromedriver                        0x0000000100185198 chromedriver + 184728
6   chromedriver                        0x0000000100185c4c chromedriver + 187468
7   chromedriver                        0x0000000100193fac chromedriver + 245676
8   chromedriver                        0x00000001001a709c chromedriver + 323740
9   chromedriver                        0x0000000100186294 chromedriver + 189076
10  chromedriver   

Failed to scrape account 422901: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x0000000100baaa80 chromedriver + 4385408
1   chromedriver                        0x0000000100ba338c chromedriver + 4354956
2   chromedriver                        0x00000001007c0b0c chromedriver + 281356
3   chromedriver                        0x00000001007b9e9c chromedriver + 253596
4   chromedriver                        0x00000001007aba5c chromedriver + 195164
5   chromedriver                        0x00000001007ace18 chromedriver + 200216
6   chromedriver                        0x00000001007abd78 chromedriver + 195960
7   chromedriver                        0x00000001007ab40c chromedriver + 193548
8   chromedriver                        0x00000001007ab3b8 chromedriver + 193464
9   chromedriver                        0x00000001007a9198 chromedriver + 184728
10  chromedriver                    

Failed to scrape account 422905: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x00000001006c2a80 chromedriver + 4385408
1   chromedriver                        0x00000001006bb38c chromedriver + 4354956
2   chromedriver                        0x00000001002d8b0c chromedriver + 281356
3   chromedriver                        0x00000001002d1e9c chromedriver + 253596
4   chromedriver                        0x00000001002c3a5c chromedriver + 195164
5   chromedriver                        0x00000001002c4e18 chromedriver + 200216
6   chromedriver                        0x00000001002c3d78 chromedriver + 195960
7   chromedriver                        0x00000001002c340c chromedriver + 193548
8   chromedriver                        0x00000001002c33b8 chromedriver + 193464
9   chromedriver                        0x00000001002c1198 chromedriver + 184728
10  chromedriver                    

...

Failed to scrape account 424822: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x0000000100e86a80 chromedriver + 4385408
1   chromedriver                        0x0000000100e7f38c chromedriver + 4354956
2   chromedriver                        0x0000000100a9cb0c chromedriver + 281356
3   chromedriver                        0x0000000100a95e9c chromedriver + 253596
4   chromedriver                        0x0000000100a87a5c chromedriver + 195164
5   chromedriver                        0x0000000100a88e18 chromedriver + 200216
6   chromedriver                        0x0000000100a87d78 chromedriver + 195960
7   chromedriver                        0x0000000100a8740c chromedriver + 193548
8   chromedriver                        0x0000000100a873b8 chromedriver + 193464
9   chromedriver                        0x0000000100a85198 chromedriver + 184728
10  chromedriver                    

Failed to scrape account 424821: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x00000001045cea80 chromedriver + 4385408
1   chromedriver                        0x00000001045c738c chromedriver + 4354956
2   chromedriver                        0x00000001041e4b0c chromedriver + 281356
3   chromedriver                        0x00000001041dde9c chromedriver + 253596
4   chromedriver                        0x00000001041cfa5c chromedriver + 195164
5   chromedriver                        0x00000001041d0e18 chromedriver + 200216
6   chromedriver                        0x00000001041cfd78 chromedriver + 195960
7   chromedriver                        0x00000001041cf40c chromedriver + 193548
8   chromedriver                        0x00000001041cf3b8 chromedriver + 193464
9   chromedriver                        0x00000001041cd198 chromedriver + 184728
10  chromedriver                    

Failed to scrape account 424829: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x000000010511aa80 chromedriver + 4385408
1   chromedriver                        0x000000010511338c chromedriver + 4354956
2   chromedriver                        0x0000000104d30b0c chromedriver + 281356
3   chromedriver                        0x0000000104d29e9c chromedriver + 253596
4   chromedriver                        0x0000000104d1ba5c chromedriver + 195164
5   chromedriver                        0x0000000104d1ce18 chromedriver + 200216
6   chromedriver                        0x0000000104d1bd78 chromedriver + 195960
7   chromedriver                        0x0000000104d1b40c chromedriver + 193548
8   chromedriver                        0x0000000104d1b3b8 chromedriver + 193464
9   chromedriver                        0x0000000104d19198 chromedriver + 184728
10  chromedriver                    

Failed to scrape account 424835: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x0000000104dd6a80 chromedriver + 4385408
1   chromedriver                        0x0000000104dcf38c chromedriver + 4354956
2   chromedriver                        0x00000001049ecb0c chromedriver + 281356
3   chromedriver                        0x00000001049e5e9c chromedriver + 253596
4   chromedriver                        0x00000001049d7a5c chromedriver + 195164
5   chromedriver                        0x00000001049d8e18 chromedriver + 200216
6   chromedriver                        0x00000001049d7d78 chromedriver + 195960
7   chromedriver                        0x00000001049d740c chromedriver + 193548
8   chromedriver                        0x00000001049d73b8 chromedriver + 193464
9   chromedriver                        0x00000001049d5198 chromedriver + 184728
10  chromedriver                    

Failed to scrape account 424837: Message: unknown error: net::ERR_CONNECTION_REFUSED
  (Session info: chrome-headless-shell=126.0.6478.127)
Stacktrace:
0   chromedriver                        0x0000000102ef6a80 chromedriver + 4385408
1   chromedriver                        0x0000000102eef38c chromedriver + 4354956
2   chromedriver                        0x0000000102b0cb0c chromedriver + 281356
3   chromedriver                        0x0000000102b05e9c chromedriver + 253596
4   chromedriver                        0x0000000102af7a5c chromedriver + 195164
5   chromedriver                        0x0000000102af8e18 chromedriver + 200216
6   chromedriver                        0x0000000102af7d78 chromedriver + 195960
7   chromedriver                        0x0000000102af740c chromedriver + 193548
8   chromedriver                        0x0000000102af73b8 chromedriver + 193464
9   chromedriver                        0x0000000102af5198 chromedriver + 184728
10  chromedriver                    

In [1]:
import os
import time
import csv
import concurrent.futures
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from webdriver_manager.chrome import ChromeDriverManager

# Function to scrape data for a single account
def scrape_account(account_num):
    # Initialize Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--disable-notifications")
    chrome_options.add_argument("--headless")
    chrome_options.add_argument("--disable-gpu")
    chrome_options.add_argument("--window-size=1920x1080")
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")

    # Add Tor proxy settings
    chrome_options.add_argument('--proxy-server=socks5://127.0.0.1:9050')

    # Initialize the WebDriver
    driver = webdriver.Chrome(ChromeDriverManager().install(), options=chrome_options)

    try:
        website = f'https://www.thebluebook.com/iProView/{account_num}/crawford-tracey-corp/subcontractors/locations-contacts/'

        # Open the website for the current account
        driver.get(website)

        # Wait for the contact page to load completely
        try:
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3')))
        except TimeoutException:
            return None

        # Scrape specific text using the provided XPaths
        account_name = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3').text
        address = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[1]').text

        try:
            acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[2]/div[1]/a/span')
            if acc_number_element.text == 'View Phone':
                # Scroll to the element
                action = ActionChains(driver)
                action.move_to_element(acc_number_element).perform()

                # Click the element to reveal the phone number
                driver.execute_script("arguments[0].click();", acc_number_element)
                time.sleep(2)  # Wait for the number to load

                # Check if FaceTime modal appears
                is_facetime_modal = False
                try:
                    facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                    if facetime_modal.is_displayed():
                        is_facetime_modal = True
                except NoSuchElementException:
                    pass

                # If it's FaceTime modal, go back and try a different approach
                if is_facetime_modal:
                    # Go back to the previous page
                    driver.back()
                    return None
                else:
                    # Find the element containing the phone number
                    acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[2]/div[1]/a/span[2]')
            acc_number = acc_number_element.text
        except NoSuchElementException:
            acc_number = None
        company_info = driver.find_element(By.XPATH, '//*[@id="companyInfoSection"]/div/ul').text

        # Initialize website variable
        website = None

        # Scrape website if available
        try:
            website_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[3]/a')
            website = website_element.get_attribute('href')
        except NoSuchElementException:
            pass

        # Scrape industry if available
        try:
            industry_element = driver.find_element(By.XPATH, '//*[@id="proViewBreadCrumbs"]/a[3]')
            industry = industry_element.text
        except NoSuchElementException:
            industry = ''

        # Scrape contacts
        contacts = []
        for i in range(1, 8):  # There are 7 contacts based on provided XPaths
            name_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/button'
            title_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[1]'
            number_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[2]/a/span'

            try:
                name = driver.find_element(By.XPATH, name_xpath).text
                title = driver.find_element(By.XPATH, title_xpath).text

                # Check if the text is "View Phone"
                number_element = driver.find_element(By.XPATH, number_xpath)
                if number_element.text == 'View Phone':
                    # Scroll to the element
                    action = ActionChains(driver)
                    action.move_to_element(number_element).perform()

                    # Click the element to reveal the phone number
                    driver.execute_script("arguments[0].click();", number_element)
                    time.sleep(2)  # Wait for the number to load

                    # Check if FaceTime modal appears
                    is_facetime_modal = False
                    try:
                        facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                        if facetime_modal.is_displayed():
                            is_facetime_modal = True
                    except NoSuchElementException:
                        pass

                    # If it's FaceTime modal, skip this contact
                    if is_facetime_modal:
                        continue
                    else:
                        # Find the element containing the phone number
                        number_element = driver.find_element(By.XPATH, f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div[1]/div/div/div/div[2]/a[1]/span[2]')
                number = number_element.text

                contacts.append({'Name': name, 'Title': title, 'Number': number})
            except NoSuchElementException:
                continue

        # Return the scraped data
        return {'account_num': account_num, 'account_name': account_name, 'address': address, 'acc_number': acc_number, 'company_info': company_info, 'website': website, 'industry': industry, 'contacts': contacts}

    finally:
        driver.quit()

# Set the directory to save the CSV file
save_dir = '/Users/safi.uddin/Desktop/bb_scrape'
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

# Open the CSV file in write mode
with open(os.path.join(save_dir, 'contacts.csv'), 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['ID', 'Name', 'Title', 'Number', 'Account Name', 'Address', 'Account number', 'Company Info', 'Website', 'Industry']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

    # Define the range of accounts
    account_range = range(320535, 320550)

    # Initialize ThreadPoolExecutor with defined number of workers
    with concurrent.futures.ThreadPoolExecutor(max_workers=15) as executor:
        # Submit scraping tasks
        futures = {executor.submit(scrape_account, account_num): account_num for account_num in account_range}

        # Iterate over completed tasks
        for future in concurrent.futures.as_completed(futures):
            account_num = futures[future]
            try:
                result = future.result()
                if result:  # Check if scraping was successful
                    if not result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': '', 'Title': '', 'Number': '', 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
                    for contact in result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': contact['Name'], 'Title': contact['Title'], 'Number': contact['Number'], 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
            except Exception as e:
                print(f"Failed to scrape account {account_num}: {e}")

# Delay to ensure all threads finish before quitting
time.sleep(5)


Failed to scrape account 320545: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320546: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320542: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320549: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320536: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320539: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320537: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320541: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320548: File is not a zip file
Failed to scrape account 320544: WebDriver.__init__() got multiple values for argument 'options'
Failed to scrape account 320538: WebDriver.__init__() got multiple valu

In [6]:
import os
import time
import csv
import concurrent.futures
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from webdriver_manager.chrome import ChromeDriverManager

# Function to scrape data for a single account
def scrape_account(account_num):
    # Initialize Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--disable-notifications")
    chrome_options.add_argument("--headless")
    chrome_options.add_argument("--disable-gpu")
    chrome_options.add_argument("--window-size=1920x1080")
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    
    # Add Tor proxy settings
    chrome_options.add_argument('--proxy-server=socks5://127.0.0.1:9050')

    # Initialize the WebDriver
    driver = webdriver.Chrome(options=chrome_options)

    try:
        website = f'https://www.thebluebook.com/iProView/{account_num}/crawford-tracey-corp/subcontractors/locations-contacts/'

        # Open the website for the current account
        driver.get(website)

        # Wait for the contact page to load completely
        try:
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3')))
        except TimeoutException:
            return None

        # Scrape specific text using the provided XPaths
        account_name = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/h3').text
        address = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[1]').text

        try:
            acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[2]/div[1]/a/span')
            if acc_number_element.text == 'View Phone':
                # Scroll to the element
                action = ActionChains(driver)
                action.move_to_element(acc_number_element).perform()

                # C+lick the element to reveal the phone number
                driver.execute_script("arguments[0].click();", acc_number_element)
                time.sleep(2)  # Wait for the number to load

                # Check if FaceTime modal appears
                is_facetime_modal = False
                try:
                    facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                    if facetime_modal.is_displayed():
                        is_facetime_modal = True
                except NoSuchElementException:
                    pass

                # If it's FaceTime modal, go back and try a different approach
                if is_facetime_modal:
                    # Go back to the previous page
                    driver.back()
                    return None
                else:
                    # Find the element containing the phone number
                    acc_number_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div/div/div[1]/div/div/div[2]/div[1]/a/span[2]')
            acc_number = acc_number_element.text
        except NoSuchElementException:
            acc_number = None
        company_info = driver.find_element(By.XPATH, '//*[@id="companyInfoSection"]/div/ul').text

        # Initialize website variable
        website = None

        # Scrape website if available
        try:
            website_element = driver.find_element(By.XPATH, '//*[@id="locationsPage-1"]/div/div[1]/div/div[1]/div/div[1]/div[3]/a')
            website = website_element.get_attribute('href')
        except NoSuchElementException:
            pass

        # Scrape industry if available
        try:
            industry_element = driver.find_element(By.XPATH, '//*[@id="proViewBreadCrumbs"]/a[3]')
            industry = industry_element.text
        except NoSuchElementException:
            industry = ''

        # Scrape contacts
        contacts = []
        for i in range(1, 8):  # There are 7 contacts based on provided XPaths
            name_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/button'
            title_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[1]'
            number_xpath = f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div/div/div/div/div[2]/a/span'

            try:
                name = driver.find_element(By.XPATH, name_xpath).text
                title = driver.find_element(By.XPATH, title_xpath).text

                # Check if the text is "View Phone"
                number_element = driver.find_element(By.XPATH, number_xpath)
                if number_element.text == 'View Phone':
                    # Scroll to the element
                    action = ActionChains(driver)
                    action.move_to_element(number_element).perform()

                    # Click the element to reveal the phone number
                    driver.execute_script("arguments[0].click();", number_element)
                    time.sleep(2)  # Wait for the number to load

                    # Check if FaceTime modal appears
                    is_facetime_modal = False
                    try:
                        facetime_modal = driver.find_element(By.XPATH, '//*[@id="URLbar"]/div/div[2]/div/div/div/div')
                        if facetime_modal.is_displayed():
                            is_facetime_modal = True
                    except NoSuchElementException:
                        pass

                    # If it's FaceTime modal, skip this contact
                    if is_facetime_modal:
                        continue
                    else:
                        # Find the element containing the phone number
                        number_element = driver.find_element(By.XPATH, f'//*[@id="keyContactSection"]/div/div[1]/div[{i}]/div[1]/div/div/div/div[2]/a[1]/span[2]')
                number = number_element.text

                contacts.append({'Name': name, 'Title': title, 'Number': number})
            except NoSuchElementException:
                continue

        # Return the scraped data
        return {'account_num': account_num, 'account_name': account_name, 'address': address, 'acc_number': acc_number, 'company_info': company_info, 'website': website, 'industry': industry, 'contacts': contacts}

    finally:
        driver.quit()

# Set the directory to save the CSV file
save_dir = '/Users/safi.uddin/Desktop/bb_scrape'
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

# Open the CSV file in write mode
with open(os.path.join(save_dir, 'contacts.csv'), 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['ID', 'Name', 'Title', 'Number', 'Account Name', 'Address', 'Account number', 'Company Info', 'Website', 'Industry']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()

    # Define the range of accounts
    account_range = range(1780000,1785000)

    # Initialize ThreadPoolExecutor with defined number of workers
    with concurrent.futures.ThreadPoolExecutor(max_workers=15) as executor:
        # Submit scraping tasks
        futures = {executor.submit(scrape_account, account_num): account_num for account_num in account_range}

        # Iterate over completed tasks
        for future in concurrent.futures.as_completed(futures):
            account_num = futures[future]
            try:
                result = future.result()
                if result:  # Check if scraping was successful
                    if not result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': '', 'Title': '', 'Number': '', 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
                    for contact in result['contacts']:
                        writer.writerow({'ID': result['account_num'], 'Name': contact['Name'], 'Title': contact['Title'], 'Number': contact['Number'], 'Account Name': result['account_name'], 'Address': result['address'], 'Account number': result['acc_number'], 'Company Info': result['company_info'], 'Website': result['website'], 'Industry': result['industry']})
            except Exception as e:
                print(f"Failed to scrape account {account_num}: {e}")

# Delay to ensure all threads finish before quitting
time.sleep(5)


Failed to scrape account 1780197: Message: unknown error: net::ERR_SOCKS_CONNECTION_FAILED
  (Session info: chrome=131.0.6778.109)
Stacktrace:
0   chromedriver                        0x0000000102c13b08 cxxbridge1$str$ptr + 3651580
1   chromedriver                        0x0000000102c0c358 cxxbridge1$str$ptr + 3620940
2   chromedriver                        0x00000001026744b4 cxxbridge1$string$len + 89224
3   chromedriver                        0x000000010266d8c8 cxxbridge1$string$len + 61596
4   chromedriver                        0x000000010265f9f8 cxxbridge1$string$len + 4556
5   chromedriver                        0x00000001026613b0 cxxbridge1$string$len + 11140
6   chromedriver                        0x000000010265fda4 cxxbridge1$string$len + 5496
7   chromedriver                        0x000000010265f604 cxxbridge1$string$len + 3544
8   chromedriver                        0x000000010265f550 cxxbridge1$string$len + 3364
9   chromedriver                        0x000000010265d2dc cor

Failed to scrape account 1784690: HTTPConnectionPool(host='localhost', port=51393): Read timed out. (read timeout=120)
